In [1]:
import pandas as pd
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
from pandas import DataFrame
from cmapPy.pandasGEXpress.parse import parse
from scipy.stats import hypergeom
from tqdm import tqdm
import mysql.connector

C:\Users\Usuario\anaconda3\lib\site-packages\pandas\core\computation\expressions.py:20: UserWarning: Pandas requires version '2.7.3' or newer of 'numexpr' (version '2.7.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED


In [2]:
disnet_db_ares = mysql.connector.connect(
  host="138.4.130.153",
  port = "30602",
  user="disnet_user",
  password="tYkX4JxV8p79",
  database="disnet_drugslayer"
)

 

disnet_mysql_cursor = disnet_db_ares.cursor()

In [3]:
q1 = """SELECT * FROM disnet_drugslayer.drug """

In [4]:
drug_disnet =pd.read_sql(q1, con=disnet_db_ares)

<ipython-input-4-6f46a91a900f>:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  drug_disnet =pd.read_sql(q1, con=disnet_db_ares)


In [5]:
pertub_id = pd.read_csv("./GSE92742_Broad_LINCS_pert_info.txt", sep="\t", dtype=str)

In [6]:
len(pertub_id["pert_iname"].unique())

28957

In [17]:
pertub_id_filter = pertub_id[pertub_id["is_touchstone"]== "1"]

In [18]:
pertub_id_filter_cp = pertub_id_filter[pertub_id_filter["pert_type"] =="trt_cp"]

In [19]:
len(pertub_id_filter_cp["pert_iname"].unique())

2429

In [20]:
drug_common_inchi = drug_disnet.merge(pertub_id_filter_cp, on ="inchi_key")

In [21]:
pertub_id_filter_cp['drug_name'] = pertub_id_filter_cp['pert_iname'].str.upper() 

<ipython-input-21-bd692c32d11c>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pertub_id_filter_cp['drug_name'] = pertub_id_filter_cp['pert_iname'].str.upper()


In [22]:
drug_common_name = drug_disnet.merge(pertub_id_filter_cp, on ="drug_name")

In [23]:
drug_common_name_fil = drug_common_name[["drug_id","drug_name"]]

In [24]:
drug_common_inchi_fil = drug_common_inchi[["drug_id","drug_name"]]

In [25]:
drugs_all_disnet_clue = pd.concat([drug_common_name,drug_common_inchi]).drop_duplicates()

In [26]:
drugs_all_disnet_clue

drug_id  source_id               drug_name  molecular_type  \
0    CHEMBL1000          1              CETIRIZINE  Small molecule   
1    CHEMBL1004          1              DOXYLAMINE  Small molecule   
2    CHEMBL1008          1                BEPRIDIL  Small molecule   
3     CHEMBL101          1          PHENYLBUTAZONE  Small molecule   
4    CHEMBL1017          1             TELMISARTAN  Small molecule   
..          ...        ...                     ...             ...   
642   CHEMBL989          1  FLUOCINOLONE ACETONIDE  Small molecule   
643   CHEMBL991          1               STAVUDINE  Small molecule   
644   CHEMBL996          1               CEFOXITIN  Small molecule   
645  CHEMBL9967          1             PIRENZEPINE  Small molecule   
646   CHEMBL998          1              LORATADINE  Small molecule   

                                    chemical_structure  \
0          O=C(O)COCCN1CCN(C(c2ccccc2)c2ccc(Cl)cc2)CC1   
1                       CN(C)CCOC(C)(c1ccccc1)c1ccccn1   
2              CC(C)COCC(CN(Cc1ccccc1)c1ccccc1)N1CCCC1   
3                CCCCC1C(=O)N(c2ccccc2)N(c2ccccc2)C1=O   
4    CCCc1nc2c(C)cc(-c3nc4ccccc4n3C)cc2n1Cc1ccc(-c2...   
..                                                 ...   
642  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...   
643          Cc1cn([C@H]2C=C[C@@H](CO)O2)c(=O)[nH]c1=O   
644  CO[C@@]1(NC(=O)Cc2cccs2)C(=O)N2C(C(=O)O)=C(COC...   
645         CN1CCN(CC(=O)N2c3ccccc3C(=O)Nc3cccnc32)CC1   
646       CCOC(=O)N1CCC(=C2c3ccc(Cl)cc3CCc3cccnc32)CC1   

                     inchi_key_x        pert_id      pert_iname pert_type  \
0    ZKLPARSLTMPFCP-UHFFFAOYSA-N  BRD-A42571354      cetirizine    trt_cp   
1    HCFDWZZGGLSKEP-UHFFFAOYSA-N  BRD-A44008656      doxylamine    trt_cp   
2    UIEATEWHFDRYRU-UHFFFAOYSA-N  BRD-A91008255        bepridil    trt_cp   
3    VYMDGNCVAMGZFE-UHFFFAOYSA-N  BRD-K10843433  phenylbutazone    trt_cp   
4    RMMXLENWKUUMAY-UHFFFAOYSA-N  BRD-K73999723     telmisartan    trt_cp   
..                           ...            ...             ...       ...   
642                          NaN  BRD-K94353609    fluocinolone    trt_cp   
643                          NaN  BRD-K93880783       stavudine    trt_cp   
644                          NaN  BRD-K70976396       cefoxitin    trt_cp   
645                          NaN  BRD-K89375097     pirenzepine    trt_cp   
646                          NaN  BRD-K82795137      loratadine    trt_cp   

    is_touchstone inchi_key_prefix                  inchi_key_y  \
0               1   ZKLPARSLTMPFCP  ZKLPARSLTMPFCP-UHFFFAOYSA-N   
1               1   HCFDWZZGGLSKEP  HCFDWZZGGLSKEP-UHFFFAOYSA-N   
2               1   UIEATEWHFDRYRU  UIEATEWHFDRYRU-UHFFFAOYSA-N   
3               1   VYMDGNCVAMGZFE  VYMDGNCVAMGZFE-UHFFFAOYSA-N   
4               1   RMMXLENWKUUMAY  RMMXLENWKUUMAY-UHFFFAOYSA-N   
..            ...              ...                          ...   
642             1   FEBLZLNTKCEFIT                          NaN   
643             1   XNKLLVCARDGLGL                          NaN   
644             1   WZOZEZRFJCJXNZ                          NaN   
645             1   RMHMFHUVIITRHF                          NaN   
646             1   JCCNYMKQOSZNPW                          NaN   

                                      canonical_smiles pubchem_cid  \
0          OC(=O)COCCN1CCN(CC1)C(c1ccccc1)c1ccc(Cl)cc1        -666   
1                       CN(C)CCOC(C)(c1ccccc1)c1ccccn1        -666   
2              CC(C)COCC(CN(Cc1ccccc1)c1ccccc1)N1CCCC1        -666   
3                CCCCC1C(=O)N(N(C1=O)c1ccccc1)c1ccccc1        4781   
4    CCCc1nc2c(C)cc(cc2n1Cc1ccc(cc1)-c1ccccc1C(O)=O...       65999   
..                                                 ...         ...   
642  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...        6215   
643          Cc1cn([C@@H]2O[C@H](CO)C=C2)c(=O)[nH]c1=O       18283   
644  CO[C@]1(NC(=O)Cc2cccs2)[C@H]2SCC(COC(N)=O)=C(N...    23667300   
645         CN1CCN(CC(=O)N2c3ccccc3C(=O)

In [27]:
drugs_disnet_clue = pd.concat([drug_common_name_fil,drug_common_inchi_fil]).drop_duplicates()

In [28]:
drugs_disnet_clue

drug_id               drug_name
0    CHEMBL1000              CETIRIZINE
1    CHEMBL1004              DOXYLAMINE
2    CHEMBL1008                BEPRIDIL
3     CHEMBL101          PHENYLBUTAZONE
4    CHEMBL1017             TELMISARTAN
..          ...                     ...
562   CHEMBL776          METAPROTERENOL
583   CHEMBL829         METHYLPROMAZINE
603   CHEMBL867           IOPANOIC ACID
606   CHEMBL869           NITROFURAZONE
642   CHEMBL989  FLUOCINOLONE ACETONIDE

[827 rows x 2 columns]

In [29]:
q2 = """SELECT * FROM disnet_drugslayer.ATC_code"""

In [30]:
drug_atc =pd.read_sql(q2, con=disnet_db_ares)

<ipython-input-30-81cdba29d433>:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  drug_atc =pd.read_sql(q2, con=disnet_db_ares)


In [31]:
drug_atc

drug_id ATC_code_id  source_id
0       CHEMBL1000     R06AE07          1
1     CHEMBL100116     N02AD01          1
2       CHEMBL1004     R06AA09          1
3       CHEMBL1004     R06AA59          1
4       CHEMBL1005     N01AH06          1
...            ...         ...        ...
3218     CHEMBL991     J05AF04          1
3219     CHEMBL996     J01DC01          1
3220    CHEMBL9967     A02BX03          1
3221     CHEMBL997     M05BA06          1
3222     CHEMBL998     R06AX13          1

[3223 rows x 3 columns]

In [32]:
atc_class = drugs_disnet_clue.merge(drug_atc,on="drug_id")

In [33]:
atc_class['index'] = atc_class['ATC_code_id'].astype(str).str[0]
atc_class

drug_id               drug_name ATC_code_id  source_id index
0     CHEMBL1000              CETIRIZINE     R06AE07          1     R
1     CHEMBL1004              DOXYLAMINE     R06AA09          1     R
2     CHEMBL1004              DOXYLAMINE     R06AA59          1     R
3     CHEMBL1008                BEPRIDIL     C08EA02          1     C
4      CHEMBL101          PHENYLBUTAZONE     M01AA01          1     M
...          ...                     ...         ...        ...   ...
1125   CHEMBL869           NITROFURAZONE     S02AA02          1     S
1126   CHEMBL989  FLUOCINOLONE ACETONIDE     C05AA10          1     C
1127   CHEMBL989  FLUOCINOLONE ACETONIDE     D07AC04          1     D
1128   CHEMBL989  FLUOCINOLONE ACETONIDE     S01BA15          1     S
1129   CHEMBL989  FLUOCINOLONE ACETONIDE     S02BA08          1     S

[1130 rows x 5 columns]

In [34]:
atc_class[atc_class["index"]== "L"]

drug_id                    drug_name ATC_code_id  source_id index
57       CHEMBL1117                   IDARUBICIN     L01DB06          1     L
74    CHEMBL1173055                    RUCAPARIB     L01XX55          1     L
75    CHEMBL1173655                     AFATINIB     L01XE13          1     L
79        CHEMBL118                    CELECOXIB     L01XX33          1     L
93    CHEMBL1200374                   EXEMESTANE     L02BG06          1     L
...             ...                          ...         ...        ...   ...
1004       CHEMBL98                   VORINOSTAT     L01XX38          1     L
1057  CHEMBL1651906                 STREPTOZOCIN     L01AD04          1     L
1081    CHEMBL46286    OMACETAXINE MEPESUCCINATE     L01XX40          1     L
1103      CHEMBL601          AMINOLEVULINIC ACID     L01XD04          1     L
1114      CHEMBL717  MEDROXYPROGESTERONE ACETATE     L02AB02          1     L

[99 rows x 5 columns]

In [35]:
### repito el proceso con los datos que tienen las claves para buscar en clue

In [36]:
atc_class_all = drugs_all_disnet_clue.merge(drug_atc,on="drug_id")

In [37]:
atc_class_all

drug_id  source_id_x               drug_name  molecular_type  \
0     CHEMBL1000            1              CETIRIZINE  Small molecule   
1     CHEMBL1000            1              CETIRIZINE  Small molecule   
2     CHEMBL1004            1              DOXYLAMINE  Small molecule   
3     CHEMBL1004            1              DOXYLAMINE  Small molecule   
4     CHEMBL1004            1              DOXYLAMINE  Small molecule   
...          ...          ...                     ...             ...   
1840   CHEMBL869            1           NITROFURAZONE  Small molecule   
1841   CHEMBL989            1  FLUOCINOLONE ACETONIDE  Small molecule   
1842   CHEMBL989            1  FLUOCINOLONE ACETONIDE  Small molecule   
1843   CHEMBL989            1  FLUOCINOLONE ACETONIDE  Small molecule   
1844   CHEMBL989            1  FLUOCINOLONE ACETONIDE  Small molecule   

                                     chemical_structure  \
0           O=C(O)COCCN1CCN(C(c2ccccc2)c2ccc(Cl)cc2)CC1   
1           O=C(O)COCCN1CCN(C(c2ccccc2)c2ccc(Cl)cc2)CC1   
2                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1   
3                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1   
4                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1   
...                                                 ...   
1840                  NC(=O)N/N=C/c1ccc([N+](=O)[O-])o1   
1841  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...   
1842  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...   
1843  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...   
1844  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...   

                      inchi_key_x        pert_id    pert_iname pert_type  \
0     ZKLPARSLTMPFCP-UHFFFAOYSA-N  BRD-A42571354    cetirizine    trt_cp   
1                             NaN  BRD-A42571354    cetirizine    trt_cp   
2     HCFDWZZGGLSKEP-UHFFFAOYSA-N  BRD-A44008656    doxylamine    trt_cp   
3     HCFDWZZGGLSKEP-UHFFFAOYSA-N  BRD-A44008656    doxylamine    trt_cp   
4                             NaN  BRD-A44008656    doxylamine    trt_cp   
...                           ...            ...           ...       ...   
1840                          NaN  BRD-K79092138    nitrofural    trt_cp   
1841                          NaN  BRD-K94353609  fluocinolone    trt_cp   
1842                          NaN  BRD-K94353609  fluocinolone    trt_cp   
1843                          NaN  BRD-K94353609  fluocinolone    trt_cp   
1844                          NaN  BRD-K94353609  fluocinolone    trt_cp   

     is_touchstone inchi_key_prefix                  inchi_key_y  \
0                1   ZKLPARSLTMPFCP  ZKLPARSLTMPFCP-UHFFFAOYSA-N   
1                1   ZKLPARSLTMPFCP                          NaN   
2                1   HCFDWZZGGLSKEP  HCFDWZZGGLSKEP-UHFFFAOYSA-N   
3                1   HCFDWZZGGLSKEP  HCFDWZZGGLSKEP-UHFFFAOYSA-N   
4                1   HCFDWZZGGLSKEP                          NaN   
...            ...              ...                          ...   
1840             1   IAIWVQXQOWNYOU                          NaN   
1841             1   FEBLZLNTKCEFIT                          NaN   
1842             1   FEBLZLNTKCEFIT                          NaN   
1843             1   FEBLZLNTKCEFIT                          NaN   
1844             1   FEBLZLNTKCEFIT                          NaN   

                                       canonical_smiles pubchem_cid  \
0           OC(=O)COCCN1CCN(CC1)C(c1ccccc1)c1ccc(Cl)cc1        -666   
1           OC(=O)COCCN1CCN(CC1)C(c1ccccc1)c1ccc(Cl)cc1        -666   
2                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1        -666   
3                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1        -666   
4                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1        -666   
...                                                 ...         ...   
1840                  NC(=O)N/N=C/c1ccc(o1)[N+](=O)[O-]        -666   
1841  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...        6215   
1842  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)..

In [38]:
atc_class_all['index'] = atc_class_all['ATC_code_id'].astype(str).str[0]
atc_class_all

drug_id  source_id_x               drug_name  molecular_type  \
0     CHEMBL1000            1              CETIRIZINE  Small molecule   
1     CHEMBL1000            1              CETIRIZINE  Small molecule   
2     CHEMBL1004            1              DOXYLAMINE  Small molecule   
3     CHEMBL1004            1              DOXYLAMINE  Small molecule   
4     CHEMBL1004            1              DOXYLAMINE  Small molecule   
...          ...          ...                     ...             ...   
1840   CHEMBL869            1           NITROFURAZONE  Small molecule   
1841   CHEMBL989            1  FLUOCINOLONE ACETONIDE  Small molecule   
1842   CHEMBL989            1  FLUOCINOLONE ACETONIDE  Small molecule   
1843   CHEMBL989            1  FLUOCINOLONE ACETONIDE  Small molecule   
1844   CHEMBL989            1  FLUOCINOLONE ACETONIDE  Small molecule   

                                     chemical_structure  \
0           O=C(O)COCCN1CCN(C(c2ccccc2)c2ccc(Cl)cc2)CC1   
1           O=C(O)COCCN1CCN(C(c2ccccc2)c2ccc(Cl)cc2)CC1   
2                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1   
3                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1   
4                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1   
...                                                 ...   
1840                  NC(=O)N/N=C/c1ccc([N+](=O)[O-])o1   
1841  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...   
1842  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...   
1843  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...   
1844  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...   

                      inchi_key_x        pert_id    pert_iname pert_type  \
0     ZKLPARSLTMPFCP-UHFFFAOYSA-N  BRD-A42571354    cetirizine    trt_cp   
1                             NaN  BRD-A42571354    cetirizine    trt_cp   
2     HCFDWZZGGLSKEP-UHFFFAOYSA-N  BRD-A44008656    doxylamine    trt_cp   
3     HCFDWZZGGLSKEP-UHFFFAOYSA-N  BRD-A44008656    doxylamine    trt_cp   
4                             NaN  BRD-A44008656    doxylamine    trt_cp   
...                           ...            ...           ...       ...   
1840                          NaN  BRD-K79092138    nitrofural    trt_cp   
1841                          NaN  BRD-K94353609  fluocinolone    trt_cp   
1842                          NaN  BRD-K94353609  fluocinolone    trt_cp   
1843                          NaN  BRD-K94353609  fluocinolone    trt_cp   
1844                          NaN  BRD-K94353609  fluocinolone    trt_cp   

     is_touchstone inchi_key_prefix                  inchi_key_y  \
0                1   ZKLPARSLTMPFCP  ZKLPARSLTMPFCP-UHFFFAOYSA-N   
1                1   ZKLPARSLTMPFCP                          NaN   
2                1   HCFDWZZGGLSKEP  HCFDWZZGGLSKEP-UHFFFAOYSA-N   
3                1   HCFDWZZGGLSKEP  HCFDWZZGGLSKEP-UHFFFAOYSA-N   
4                1   HCFDWZZGGLSKEP                          NaN   
...            ...              ...                          ...   
1840             1   IAIWVQXQOWNYOU                          NaN   
1841             1   FEBLZLNTKCEFIT                          NaN   
1842             1   FEBLZLNTKCEFIT                          NaN   
1843             1   FEBLZLNTKCEFIT                          NaN   
1844             1   FEBLZLNTKCEFIT                          NaN   

                                       canonical_smiles pubchem_cid  \
0           OC(=O)COCCN1CCN(CC1)C(c1ccccc1)c1ccc(Cl)cc1        -666   
1           OC(=O)COCCN1CCN(CC1)C(c1ccccc1)c1ccc(Cl)cc1        -666   
2                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1        -666   
3                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1        -666   
4                        CN(C)CCOC(C)(c1ccccc1)c1ccccn1        -666   
...                                                 ...         ...   
1840                  NC(=O)N/N=C/c1ccc(o1)[N+](=O)[O-]        -666   
1841  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)...        6215   
1842  CC1(C)O[C@@H]2C[C@H]3[C@@H]4C[C@H](F)C5=CC(=O)..

In [39]:
atc_cancer = atc_class_all[atc_class_all["index"]== "L"]

In [43]:
atc_cancer = atc_cancer[["pert_iname","drug_name","drug_id","pert_id"]].drop_duplicates()

In [44]:
len(atc_cancer["pert_iname"].unique())

95

In [45]:
atc_cancer.to_csv("drugs_cancer_clue.csv")